# Введение в анализ данных
## НИУ ВШЭ, 2019-2020 учебный год

### Домашнее задание №3

Задание выполнил(а): (впишите свои фамилию и имя): Пучкова Арина

### Общая информация

__Дата выдачи:__ 06.04.2020

__Дедлайн:__ 23:59 20.04.2020


### Оценивание и штрафы

Оценка за ДЗ вычисляется по следующей формуле:

$$
min(\text{points}, 18)  \times 10 / 18,
$$

где points — количество баллов за обязательную часть, которое вы набрали. Максимальное число баллов, которое можно получить за обязательную часть — 18, за каждые полтора балла сверху вы получите 1 бонусный балл (максимум 2). Также вы можете использовать бонусные баллы, которые накопили ранее.

За сдачу задания позже срока на итоговую оценку за задание накладывается штраф в размере 1 балл в день, но получить отрицательную оценку нельзя.

__Внимание!__ Домашнее задание выполняется самостоятельно. «Похожие» решения считаются плагиатом и все задействованные студенты (в том числе те, у кого списали) не могут получить за него больше 0 баллов.

### Формат сдачи

Загрузка файлов с решениями происходит в системе [Anytask](https://anytask.org/).

Инвайт для группы ИАД-6: rd5CNrr

Перед отправкой перезагрузите ноутбук и проверьте, что все ячейки могут быть последовательно выполнены. Ноутбук должен запускаться с использованием python 3.6+

### Подготовка данных

In [1]:
import numpy as np
import pandas as pd

import matplotlib.pyplot as plt
%matplotlib inline

from tqdm import tqdm

In [398]:
# Качаем датасет

!wget https://www.dropbox.com/s/tg55q9mrziroyrs/train_subset.csv

https://www.dropbox.com/s/tg55q9mrziroyrs/train_subset.csv: HTTPS support not compiled in.


### Данные

Мы имеем дело с данными с торговой платформы Avito.
Для каждого товара представлены следующие параметры:
 - title
 - description
 - Category_name
 - Category

Имеется информация об объектах 50 классов.
Задача: по новым объектам (title, description) предсказать Category.
(Очевидно, что параметр Category_name для предсказания классов использовать нельзя)

In [2]:
data = pd.read_csv("train_subset.csv", index_col='id')

data.head()

title  \
id                                   
382220                    Прихожая   
397529   Кордиант 215/55/16 Летние   
584569                        Стол   
2513100                 Комбинезон   
1091886                   Ветровка   

                                               description  \
id                                                           
382220                           В хорошем состоянии. Торг   
397529   Кордиант 215/55/16 Летние/\n /\nАртикул: 1737l...   
584569   Стол, 2 рабочих места . Стол серого цвета, в д...   
2513100                                       Размер-42/44   
1091886                                          На 2 года   

                     Category_name  Category  
id                                            
382220           Мебель и интерьер        20  
397529       Запчасти и аксессуары        10  
584569           Мебель и интерьер        20  
2513100  Одежда, обувь, аксессуары        27  
1091886     Детская одежда и обувь        29

In [3]:
data.shape

(30000, 4)

In [4]:
X = data[['title', 'description']].to_numpy()
y = data['Category'].to_numpy()

del data

Сразу разделим выборку на train и test.
Никакие данные из test для обучения использовать нельзя!

In [5]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)

In [6]:
X_train[:5]

array([['Сапоги 46 размер новые', 'Сапоги 46 размер новые'],
       ['Светильники потолочный swarovski',
        'светильники потолочные swarovski 6 штук , цена за штуку. В эксплуатации 2 года , продаются в связи со сменой интерьера в квартире'],
       ['iPhone 7 plus 128GB Red красный в наличии',
        '\xa0/\n/\n Данная цена только для подписчиков Instagram: iQmac/\n/\n Новый красный айфон 7 Plus в наличии это элегантный и мощный смартфон, который готов в полной мере раскрыть новые возможности iOS 10. Аппарат с 4-ядерным процессором А10 и 3 ГБ ОЗУ с легкостью решает самые ресурсоемкие задачи, позволяя наслаждаться быстродействием «тяжелых» приложений и игр на 5,5-дюймовом дисплее. Аппарат получил экран, как у iPad Pro, так что картинка теперь соответствует кинематографическому стандарту.'],
       ['Пион Ирис Ромашка рассада',
        'Пион куст 500 р ( более 10 шт)/\nСаженец/ корень 100р/\nРастут у нас более 70 лет/\nРозовые, бордовые и белые/\nНа фото цветы 2018г/\nП. Зубчанинов

In [7]:
y_train[:5]

array([ 27,  20,  84, 106,  27])

In [8]:
X_train[10][1]

'Продам иж планета 3 , 76 год ,  ( стоит на старом учёте , документы утеряны ) на ходу , хорошее состояние , все интересующие вопросы по телефону ( С родной коляской на 3 тысячи дороже ) .  Торга не будет .'

### Токенизация (1 балл)


Токенизация -- разбиение текста на мелкие части, которые можно обработать машинными методами.
Можно использовать разные алгоритмы токенизации.
Можете использовать WordPunctTokenizer или подобрать какой-то другой, если считаете, что он лучше подойдет для этой задачи.


In [9]:
from nltk.tokenize import WordPunctTokenizer

tokenizer = WordPunctTokenizer()

text = 'Здраствуйте. Я, Кирилл. Хотел бы чтобы вы сделали игру, 3Д-экшон суть такова...'

print("before:", text,)
print("after:", tokenizer.tokenize(text.lower()),)

before: Здраствуйте. Я, Кирилл. Хотел бы чтобы вы сделали игру, 3Д-экшон суть такова...
after: ['здраствуйте', '.', 'я', ',', 'кирилл', '.', 'хотел', 'бы', 'чтобы', 'вы', 'сделали', 'игру', ',', '3д', '-', 'экшон', 'суть', 'такова', '...']


__Задание:__ реализуйте функцию ниже

In [10]:
def preprocess(text: str) -> str:
    
    aux = tokenizer.tokenize(text.lower()) 
    return " ".join(aux)

In [11]:
X_train = [[preprocess(x[0]), preprocess(x[1])] for x in X_train] 

In [12]:
X_test = [[preprocess(x[0]), preprocess(x[1])] for x in X_test] 

In [13]:
assert X_train[10][1] == 'продам иж планета 3 , 76 год , ( стоит на старом учёте , документы утеряны ) на ходу , хорошее состояние , все интересующие вопросы по телефону ( с родной коляской на 3 тысячи дороже ) . торга не будет .'

In [14]:
X_train[:5]

[['сапоги 46 размер новые', 'сапоги 46 размер новые'],
 ['светильники потолочный swarovski',
  'светильники потолочные swarovski 6 штук , цена за штуку . в эксплуатации 2 года , продаются в связи со сменой интерьера в квартире'],
 ['iphone 7 plus 128gb red красный в наличии',
  '/ / данная цена только для подписчиков instagram : iqmac / / новый красный айфон 7 plus в наличии это элегантный и мощный смартфон , который готов в полной мере раскрыть новые возможности ios 10 . аппарат с 4 - ядерным процессором а10 и 3 гб озу с легкостью решает самые ресурсоемкие задачи , позволяя наслаждаться быстродействием « тяжелых » приложений и игр на 5 , 5 - дюймовом дисплее . аппарат получил экран , как у ipad pro , так что картинка теперь соответствует кинематографическому стандарту .'],
 ['пион ирис ромашка рассада',
  'пион куст 500 р ( более 10 шт )/ саженец / корень 100р / растут у нас более 70 лет / розовые , бордовые и белые / на фото цветы 2018г / п . зубчаниновка / либо пл . революции / есть

### BOW (3 балла)

Один из традиционных подходов -- построение bag of words.

Метод состоит в следующем:

 - Составить словарь самых часто встречающихся слов в train data
 - Для каждого примера из train посчитать, сколько раз каждое слово из словаря в нём встречается


 В sklearn есть CountVectorizer, но в этом задании его использовать нельзя.

__Задание:__ создайте словарь, где в соответствии каждому токену стоит количество раз, которое оно встретилось в X_train

In [15]:
import sys #это для того, чтоб потом целиком показывались векторы
import numpy 
numpy.set_printoptions(threshold = sys.maxsize)

In [16]:
allsent = [sent for object in X_train for sent in object] #все предложения

In [17]:
allsent[:5]

['сапоги 46 размер новые',
 'сапоги 46 размер новые',
 'светильники потолочный swarovski',
 'светильники потолочные swarovski 6 штук , цена за штуку . в эксплуатации 2 года , продаются в связи со сменой интерьера в квартире',
 'iphone 7 plus 128gb red красный в наличии']

In [18]:
allwords = [tokenizer.tokenize(sent) for sent in allsent]

In [19]:
allwords = [word for sent in allwords for word in sent] #тут все слова из title и description

In [20]:
allwords[:20]

['сапоги',
 '46',
 'размер',
 'новые',
 'сапоги',
 '46',
 'размер',
 'новые',
 'светильники',
 'потолочный',
 'swarovski',
 'светильники',
 'потолочные',
 'swarovski',
 '6',
 'штук',
 ',',
 'цена',
 'за',
 'штуку']

In [21]:
tokens = {}
for word in allwords: 
    tokens[word] = tokens.get(word, 0) + 1

In [22]:
assert tokens['сапоги'] == 454

__Задание:__ выведите 10 самых частотных и 10 самых редких токенов

In [23]:
bottom10 = sorted(tokens.items(),key = lambda kv:kv[1])[:10]
bottom10 #самые редкие

[('iqmac', 1),
 ('ядерным', 1),
 ('ресурсоемкие', 1),
 ('быстродействием', 1),
 ('кинематографическому', 1),
 ('ирис', 1),
 ('саженец', 1),
 ('корень', 1),
 ('зубчаниновка', 1),
 ('боярышник', 1)]

In [24]:
top10 = sorted(tokens.items(),key = lambda kv:kv[1])[-10:]
top10 #ожидамо, это знаки пунктуации и разные предлоги и союзы. 

[('с', 12860),
 (':', 15098),
 ('./', 17639),
 ('на', 19465),
 ('и', 21714),
 ('в', 28337),
 ('-', 36840),
 ('.', 65624),
 (',', 79117),
 ('/', 85802)]

__Задание:__ оставьте в словаре только топ 10000 самых частотных токенов

In [25]:
from collections import Counter

In [26]:
count = Counter(tokens) 

In [27]:
most_common = dict(count.most_common(10000))

In [28]:
most_common["/"]

85802

In [34]:
len(most_common)

10000

__Задание:__ реализуйте функцию, которая предложение переводит в вектор из чисел. То есть каждому слову из словаря сопоставляется количество раз, которое оно встретилось в предложении.

In [63]:
def text_to_bow(text: str) -> np.array:
    """
    Возвращает вектор, где для каждого слова из most_common
    указано количество его употреблений
    input: строка
    output: вектор размерности словаря
    """  
    new = []
    tokens = text.split()
    for word in most_common.keys():
        new.append(tokens.count(word))
    return new

In [64]:
text_to_bow("/ / данная цена только для подписчиков instagram : iqmac / / новый красный айфон 7 plus в наличии это элегантный и мощный смартфон , который готов в полной мере раскрыть новые возможности ios 10 . аппарат с 4 - ядерным процессором а10 и 3 гб озу с легкостью решает самые ресурсоемкие задачи , позволяя наслаждаться быстродействием « тяжелых » приложений и игр на 5 , 5 - дюймовом дисплее . аппарат получил экран , как у ipad pro , так что картинка теперь соответствует кинематографическому стандарту .")
            
            

[4,
 5,
 3,
 2,
 2,
 3,
 1,
 0,
 1,
 2,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 2,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,


__Задание:__ а теперь реализуйте функцию, которая преобразует наш датасет и для каждого текста из description сопоставляет вектор.

In [65]:
def items_to_bow(items: np.array) -> np.array:
    """ Для каждого товара возвращает вектор его bow """
    # Давайте для начала попробуем строить bow только из description товара
    new = [text_to_bow(item[1]) for item in items]
    return np.array(new)
        

In [66]:
X_train_bow = items_to_bow(X_train) #прогоняется долго....
X_test_bow = items_to_bow(X_test)

In [67]:
len(X_train_bow[1])

10000

In [68]:
# чтобы видеть проход по итерациям можно использовать библиотеку tqdm
# она работает примерно так
from tqdm import tqdm

for i in tqdm(range(100)):
    pass

100%|██████████| 100/100 [00:00<00:00, 1759.94it/s]


In [69]:
from sklearn.metrics import accuracy_score

### Логистическая регрессия и SVC (0.5 балла)


Теперь описание каждого товара представлено, как точка в многомерном пространстве.
Очень важно запомнить эту идею: дальше мы будем рассматривать разные способы перехода от текста к точке в пространстве.

Для BOW каждое измерение в пространстве -- какое-то слово.
Мы предполагаем, что текст описывается набором каких-то популярных слов, которые в нём встречаются, а близкие по смыслу тексты будут использовать одинаковые слова.

Обучите логистическую регрессию и SVC с базовыми параметрами.


In [70]:
from sklearn.linear_model import LogisticRegression

In [71]:
lr_model = LogisticRegression()

In [72]:
lr_model.fit(X_train_bow, y_train)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=100,
                   multi_class='warn', n_jobs=None, penalty='l2',
                   random_state=None, solver='warn', tol=0.0001, verbose=0,
                   warm_start=False)

In [73]:
assert accuracy_score(lr_model.predict(X_test_bow), y_test) > 0.7

In [74]:
accuracy_score(lr_model.predict(X_test_bow), y_test)

0.7046666666666667

In [75]:
from sklearn.svm import LinearSVC

In [76]:
svc_model = LinearSVC()

In [77]:
svc_model = LinearSVC(max_iter = 10000) #количество итераций было повышено, потому что не сходилось, но видимо не помогло
svc_model.fit(X_train_bow, y_train)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:929: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


LinearSVC(C=1.0, class_weight=None, dual=True, fit_intercept=True,
          intercept_scaling=1, loss='squared_hinge', max_iter=10000,
          multi_class='ovr', penalty='l2', random_state=None, tol=0.0001,
          verbose=0)

In [78]:
assert accuracy_score(svc_model.predict(X_test_bow), y_test) > 0.68

In [79]:
accuracy_score(svc_model.predict(X_test_bow), y_test)

0.6842222222222222

### Модификация признаков (0.5 балла)

Добавьте title товара в bow с произвольным весом, как изменится качество?

In [80]:
def title_and_description(items: np.array, weight: int):
    new = [np.array(text_to_bow(item[0]))*weight + np.array(text_to_bow(item[1])) for item in tqdm(items)]
    return np.array(new)

In [81]:
X_train_mod = title_and_description(X_train, 2)
X_test_mod = title_and_description(X_test, 2)

100%|██████████| 9000/9000 [07:13<00:00, 20.76it/s]


In [82]:
X_train_bow[5]

array([ 0, 13,  7,  2,  6,  0,  2,  0,  0,  0,  0,  0,  0,  0,  0,  1,  0,
        0,  0,  0,  0,  0,  0,  0,  1,  0,  0,  0,  0,  0,  0,  1,  0,  0,
        0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
        0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
        1,  0,  0,  1,  0,  0,  0,  0,  0,  0,  0,  2,  1,  0,  0,  0,  0,
        0,  2,  0,  0,  1,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
        0,  0,  0,  0,  1,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
        0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  1,  0,  0,  0,  0,  0,
        0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
        0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
        0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  1,  0,  0,  0,  0,  0,  0,
        0,  0,  1,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  1,  0,
        1,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
        1,  0,  0,  0,  0

In [83]:
X_train_mod[5]

array([ 2, 17,  9,  4,  6,  0,  2,  0,  0,  0,  0,  0,  0,  0,  0,  1,  2,
        0,  0,  0,  0,  0,  0,  2,  1,  0,  0,  0,  0,  0,  0,  1,  0,  2,
        0,  0,  0,  0,  2,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
        0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
        1,  0,  0,  1,  0,  0,  0,  0,  0,  0,  0,  2,  1,  0,  0,  0,  0,
        0,  4,  0,  0,  1,  0,  0,  2,  0,  0,  0,  0,  0,  0,  0,  0,  0,
        0,  0,  0,  0,  1,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
        0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  1,  0,  0,  0,  0,  0,
        0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
        0,  2,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
        0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  1,  0,  0,  0,  0,  0,  0,
        0,  0,  1,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  1,  0,
        1,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
        1,  0,  0,  0,  0

In [84]:
X_train[5]

['1 - к квартира , 33 м² , 4 / 5 эт .',
 'продаётся уютная , тёплая квартира в экологически - чистом районе города , рядом сосновый бор , всегда чистый воздух . дом 2004 г ., хорошие соседи , на площадке 2 - е квартиры , развитая инфраструктура , в шаговой доступности поликлиника , школа , тк « орбита », вещевой рынок . квартира в хорошем состоянии . подходит под ипотеку , долгов , обременений , перепланировке нет . в квартире натяжные потолки , в ванной комнате стены выполнены из влагостойких стеновых панелей . возможен обмен на квартиру в г . магнитогорске , торг .']

In [85]:
most_common

{'/': 85802,
 ',': 79117,
 '.': 65624,
 '-': 36840,
 'в': 28337,
 'и': 21714,
 'на': 19465,
 './': 17639,
 ':': 15098,
 'с': 12860,
 '(': 12157,
 'по': 10000,
 'для': 9627,
 'не': 6045,
 ')': 5782,
 '2': 5766,
 '1': 5284,
 '!': 5198,
 'до': 4541,
 'от': 4482,
 '—': 4449,
 '"': 4250,
 '3': 4071,
 '5': 4003,
 'состоянии': 3981,
 '!/': 3916,
 'у': 3855,
 'за': 3425,
 'все': 3382,
 'размер': 3320,
 'без': 3258,
 'из': 3137,
 '*': 2944,
 '4': 2939,
 'есть': 2906,
 'доставка': 2840,
 '00': 2799,
 'см': 2774,
 'к': 2681,
 'продам': 2677,
 'состояние': 2666,
 'или': 2631,
 ')/': 2471,
 '10': 2452,
 'цена': 2379,
 ':/': 2311,
 'б': 2266,
 '•': 2212,
 'наличии': 2172,
 'руб': 2147,
 '6': 2126,
 'при': 2111,
 'очень': 2064,
 'р': 1987,
 'фото': 1978,
 'новые': 1872,
 'звоните': 1858,
 'можно': 1855,
 'м': 1853,
 'запчасти': 1717,
 ';/': 1697,
 '+': 1668,
 'новый': 1626,
 '8': 1609,
 'отличном': 1577,
 '20': 1551,
 '7': 1485,
 'продаю': 1485,
 'хорошем': 1479,
 'гарантия': 1479,
 'как': 1468,
 'по

Код выше демонститует, что все работает как надо: при добавлении title с весом 2, число использования "/" стало равно 2 (вместо 0), так как в desription их не было, а в title есть один слэш

In [86]:
lr_model.fit(X_train_mod, y_train)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=100,
                   multi_class='warn', n_jobs=None, penalty='l2',
                   random_state=None, solver='warn', tol=0.0001, verbose=0,
                   warm_start=False)

In [87]:
accuracy_score(lr_model.predict(X_test_mod), y_test) 

0.7964444444444444

In [88]:
svc_model = LinearSVC()
svc_model.fit(X_train_mod, y_train)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:929: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


LinearSVC(C=1.0, class_weight=None, dual=True, fit_intercept=True,
          intercept_scaling=1, loss='squared_hinge', max_iter=1000,
          multi_class='ovr', penalty='l2', random_state=None, tol=0.0001,
          verbose=0)

In [89]:
accuracy_score(svc_model.predict(X_test_mod), y_test) 

0.7604444444444445

- Для логистической регрессии качество выросло до 0.79 (с 0.7)   
- Для СВМ – до 0.76 (с 0.68) – то есть добавлять заголовок в BOW – хорошая идея

Нормализуйте данные (`sklearn.preprocessing.normalize`) перед обучением. Что станет с качеством и почему?

In [63]:
from sklearn.preprocessing import normalize

In [64]:
X_train_norm = normalize(X_train_mod)

In [65]:
X_train_mod[1]

array([0, 2, 1, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

In [66]:
X_train_norm[1]

array([0.        , 0.33333333, 0.16666667, 0.        , 0.5       ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.16666667, 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.16666667, 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.16666667,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.16666667, 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.     

In [67]:
X_test_norm = normalize(X_test_mod)

In [68]:
lr_model.fit(X_train_norm, y_train)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=100,
                   multi_class='warn', n_jobs=None, penalty='l2',
                   random_state=None, solver='warn', tol=0.0001, verbose=0,
                   warm_start=False)

In [69]:
accuracy_score(lr_model.predict(X_test_norm), y_test) 

0.6897777777777778

In [70]:
svc_model = LinearSVC()
svc_model.fit(X_train_norm, y_train)

LinearSVC(C=1.0, class_weight=None, dual=True, fit_intercept=True,
          intercept_scaling=1, loss='squared_hinge', max_iter=1000,
          multi_class='ovr', penalty='l2', random_state=None, tol=0.0001,
          verbose=0)

In [71]:
accuracy_score(svc_model.predict(X_test_norm), y_test) 

0.8072222222222222

- Качество линейной регрессии упало с 0.79 до 0.69 при нормализации. Это могло произойти из-за того, что модель нуждается в регуляризации – у нас слишком много признаков. К тому же, изз-за регуляризации и "выравнивания" масштаба признаков, те фичи, которые модель изначально незначимы, начинют влиять на выход модели. В нашем случае: на выход модели начивают влиять не то чтобы часто встречающиеся в названии и описании товара слова. + может сказываться разница меджду масштабом признаков и отклика

- Качество СВМ наоборот выросло: с 0.76 до 0.8. Возможно, на СВМ в меньшей степени влияет разница в масштабе отклика и признаков (а при нормализации мы занизили масштаб признаков, оставив прежним масштаб отклика)

### Mystem (1 балл)

Попробуйте обучиться, используя токенизатор mystem. Сравните качество.

In [66]:
!wget http://download.cdn.yandex.net/mystem/mystem-3.0-linux3.1-64bit.tar.gz
!tar -xvf mystem-3.0-linux3.1-64bit.tar.gz
!cp mystem /bin

--2020-04-13 15:26:40--  http://download.cdn.yandex.net/mystem/mystem-3.0-linux3.1-64bit.tar.gz
Распознаётся download.cdn.yandex.net (download.cdn.yandex.net)… 5.45.205.243, 5.45.205.244, 5.45.205.241, ...
Подключение к download.cdn.yandex.net (download.cdn.yandex.net)|5.45.205.243|:80... соединение установлено.
HTTP-запрос отправлен. Ожидание ответа… 302 Found
Адрес: http://cache-mskmar04.cdn.yandex.net/download.cdn.yandex.net/mystem/mystem-3.0-linux3.1-64bit.tar.gz [переход]
--2020-04-13 15:26:41--  http://cache-mskmar04.cdn.yandex.net/download.cdn.yandex.net/mystem/mystem-3.0-linux3.1-64bit.tar.gz
Распознаётся cache-mskmar04.cdn.yandex.net (cache-mskmar04.cdn.yandex.net)… 5.45.222.28
Подключение к cache-mskmar04.cdn.yandex.net (cache-mskmar04.cdn.yandex.net)|5.45.222.28|:80... соединение установлено.
HTTP-запрос отправлен. Ожидание ответа… 200 OK
Длина: 16457938 (16M) [application/octet-stream]
Сохранение в: «mystem-3.0-linux3.1-64bit.tar.gz.1»

mystem-3.0-linux3.1 100%[============

In [131]:
pip install git+https://github.com/nlpub/pymystem3

  Cloning https://github.com/nlpub/pymystem3 to /private/var/folders/sz/p8_1lnhs2r16g1rht3z0zwrh0000gn/T/pip-req-build-awm8j9u4
  Running command git clone -q https://github.com/nlpub/pymystem3 /private/var/folders/sz/p8_1lnhs2r16g1rht3z0zwrh0000gn/T/pip-req-build-awm8j9u4
  Created wheel for pymystem3: filename=pymystem3-0.2.0-cp37-none-any.whl size=9922 sha256=ec5aca7be6afe1cd73c60c98ca7b9d97286bdb321e6b90663a65ef3ad6c48550
  Stored in directory: /private/var/folders/sz/p8_1lnhs2r16g1rht3z0zwrh0000gn/T/pip-ephem-wheel-cache-2gjhvjym/wheels/7d/75/c2/216a594291dee680749ce12c60d16125cfe1f363059e7163dc
Successfully built pymystem3
Note: you may need to restart the kernel to use updated packages.


In [16]:
from pymystem3 import Mystem

In [73]:
mystem_analyzer = Mystem(entire_input = False) #чтобы убрались еще знаки препинания и всякий мусор 

In [74]:
text = "Сейчас буду есть гречу с грибами, вот это радость!"

In [75]:
print(mystem_analyzer.lemmatize(text))

['сейчас', 'быть', 'есть', 'греча', 'с', 'гриб', 'вот', 'это', 'радость']


In [25]:
allwords_l = [mystem_analyzer.lemmatize(sent) for sent in allsent] #нужно переделать с лемматизацией все, начиная со словаря 
#самых популярных слов, так что займемся этим

In [26]:
allwords_l[:10]

[['сапог', 'размер', 'новый'],
 ['сапог', 'размер', 'новый'],
 ['светильник', 'потолочный', 'swarovski'],
 ['светильник',
  'потолочный',
  'swarovski',
  'штука',
  'цена',
  'за',
  'штука',
  'в',
  'эксплуатация',
  'год',
  'продаваться',
  'в',
  'связь',
  'со',
  'смена',
  'интерьер',
  'в',
  'квартира'],
 ['iphone', 'plus', 'red', 'красный', 'в', 'наличие'],
 ['данный',
  'цена',
  'только',
  'для',
  'подписчик',
  'instagram',
  'iqmac',
  'новый',
  'красный',
  'айфон',
  'plus',
  'в',
  'наличие',
  'это',
  'элегантный',
  'и',
  'мощный',
  'смартфон',
  'который',
  'готовый',
  'в',
  'полный',
  'мера',
  'раскрывать',
  'новый',
  'возможность',
  'ios',
  'аппарат',
  'с',
  'ядерный',
  'процессор',
  'и',
  'гб',
  'озу',
  'с',
  'легкость',
  'решать',
  'самый',
  'ресурсоемкий',
  'задача',
  'позволять',
  'наслаждаться',
  'быстродействие',
  'тяжелый',
  'приложение',
  'и',
  'игра',
  'на',
  'дюймовый',
  'дисплей',
  'аппарат',
  'получать',
  'экр

In [27]:
allwords_l = [word for sent in allwords_l for word in sent]

In [28]:
allwords_l[:10]

['сапог',
 'размер',
 'новый',
 'сапог',
 'размер',
 'новый',
 'светильник',
 'потолочный',
 'swarovski',
 'светильник']

In [29]:
lemms = {}
for lemm in allwords_l: 
    lemms[lemm] = lemms.get(lemm, 0) + 1

In [41]:
count = Counter(lemms) 

In [42]:
most_common_l = dict(count.most_common(10000))

In [43]:
most_common_l #словарь есть, надо лемматизировать текст

{'в': 28344,
 'и': 21714,
 'на': 19491,
 'с': 12863,
 'по': 10021,
 'для': 9627,
 'состояние': 6804,
 'новый': 6175,
 'не': 6056,
 'продавать': 4774,
 'весь': 4715,
 'размер': 4553,
 'до': 4552,
 'от': 4497,
 'быть': 4225,
 'цена': 4083,
 'у': 3855,
 'доставка': 3466,
 'за': 3427,
 'без': 3263,
 'вы': 3202,
 'хороший': 3162,
 'отличный': 3137,
 'из': 3137,
 'год': 3056,
 'наш': 3015,
 'запчасть': 2997,
 'наличие': 2975,
 'см': 2785,
 'магазин': 2712,
 'к': 2684,
 'мы': 2676,
 'или': 2631,
 'любой': 2591,
 '═': 2377,
 'автомобиль': 2360,
 'б': 2266,
 'квартира': 2193,
 'звонить': 2163,
 'руб': 2149,
 'при': 2115,
 'комплект': 2088,
 'очень': 2071,
 'компания': 2034,
 'гарантия': 2031,
 'работа': 2026,
 'дом': 2019,
 'р': 1987,
 'фото': 1983,
 'товар': 1942,
 'можно': 1859,
 'м': 1853,
 'мочь': 1806,
 'работать': 1801,
 'цвет': 1794,
 'ваш': 1738,
 'другой': 1707,
 'один': 1665,
 'платье': 1511,
 'телефон': 1508,
 'задний': 1505,
 'регион': 1502,
 'торг': 1494,
 'возможный': 1488,
 'под'

In [84]:
def lemm_to_bow(text: str) -> np.array:
    bow = []
    lemms = mystem_analyzer.lemmatize(text)
    for i in most_common_l.keys():
        bow.append(lemms.count(i))
    return bow

In [85]:
lemm_to_bow("В состоянии сейчас съесть люксовую гречу с грибами, вот это радость!")

[1,
 0,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,


In [86]:
def title_and_desc_l(items: np.array, weight: int):
    new = [np.array(lemm_to_bow(item[0]))*weight + np.array(lemm_to_bow(item[1])) for item in tqdm(items)]
    return np.array(new)


In [87]:
mystem_analyzer = Mystem(entire_input = False) #я тут снова инициализирую майстем, так как он у меня систематически вылетал, и 
#помогало только заново инициализировать :( 

In [88]:
X_train_lemm = title_and_desc_l(X_train, 2)
X_test_lemm = title_and_desc_l(X_test, 2)

100%|██████████| 9000/9000 [08:39<00:00, 17.31it/s]


In [89]:
lr_model.fit(X_train_lemm, y_train)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=100,
                   multi_class='warn', n_jobs=None, penalty='l2',
                   random_state=None, solver='warn', tol=0.0001, verbose=0,
                   warm_start=False)

In [90]:
accuracy_score(lr_model.predict(X_test_lemm), y_test) #хороший результат! Пока что это самая высокая accuracy для регрессии

0.8072222222222222

In [91]:
svc_model.fit(X_train_lemm, y_train)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:929: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


LinearSVC(C=1.0, class_weight=None, dual=True, fit_intercept=True,
          intercept_scaling=1, loss='squared_hinge', max_iter=1000,
          multi_class='ovr', penalty='l2', random_state=None, tol=0.0001,
          verbose=0)

In [92]:
accuracy_score(svc_model.predict(X_test_lemm), y_test) #а для svm accuracy не такой хороший, как при нормализации признаков в 
#BOW

0.7765555555555556

- Для регрессии получается самый лучший результат – 0.807 – so far. Вероятно, помогает чистать датасет от знаков препинания  
- А для СВМ качество упало с 0.8 (при нормализации) до 0.78

### TF-IDF (5 баллов)

Не все слова полезны одинаково, давайте попробуем [взвесить](http://tfidf.com/) их, чтобы отобрать более полезные.


> TF(t) = (Number of times term t appears in a document) / (Total number of terms in the document).
> 
> IDF(t) = log_e(Total number of documents / Number of documents with term t in it).


В sklearn есть TfidfVectorizer, но в этом задании его использовать нельзя. Для простоты посчитайте общий tf-idf для title и description (то есть каждому объекту надо сопоставить вектор, где как документ будет рассматриваться конкатенация title и description).

__Задание:__ составьте словарь, где каждому слову из изначального словаря будет стоять в соответствии количество документов, где это слово встретилось.

In [17]:
mystem_analyzer = Mystem(entire_input = False)

In [18]:
X_train_conc = [mystem_analyzer.lemmatize(item[0] + " " + item[1]) for item in X_train] 
    
    #title и description будут склеены. В этом задании я буду работать с леммами, так как с ними вроде хорошие результаты
    #+ при сипользовании разных токенайзеров по-разному преобразуются знаки препинания (i.e. ".)" или ".", ")"), а лемматизатор 
    #просто их убирает, что удобнее

In [19]:
mystem_analyzer = Mystem(entire_input = False)

In [20]:
X_test_conc = [mystem_analyzer.lemmatize(object[0] + " " + object[1]) for object in X_test] 

In [21]:
X_train_conc[:5]

[['сапог', 'размер', 'новый', 'сапог', 'размер', 'новый'],
 ['светильник',
  'потолочный',
  'swarovski',
  'светильник',
  'потолочный',
  'swarovski',
  'штука',
  'цена',
  'за',
  'штука',
  'в',
  'эксплуатация',
  'год',
  'продаваться',
  'в',
  'связь',
  'со',
  'смена',
  'интерьер',
  'в',
  'квартира'],
 ['iphone',
  'plus',
  'red',
  'красный',
  'в',
  'наличие',
  'данный',
  'цена',
  'только',
  'для',
  'подписчик',
  'instagram',
  'iqmac',
  'новый',
  'красный',
  'айфон',
  'plus',
  'в',
  'наличие',
  'это',
  'элегантный',
  'и',
  'мощный',
  'смартфон',
  'который',
  'готовый',
  'в',
  'полный',
  'мера',
  'раскрывать',
  'новый',
  'возможность',
  'ios',
  'аппарат',
  'с',
  'ядерный',
  'процессор',
  'и',
  'гб',
  'озу',
  'с',
  'легкость',
  'решать',
  'самый',
  'ресурсоемкий',
  'задача',
  'позволять',
  'наслаждаться',
  'быстродействие',
  'тяжелый',
  'приложение',
  'и',
  'игра',
  'на',
  'дюймовый',
  'дисплей',
  'аппарат',
  'получать

In [44]:
occurences_doc = {} 
for word in most_common_l.keys(): #словарь из прошлого задания 
    count = 0
    for line in X_train_conc: 
        if word in line: 
            count += 1
        continue
    occurences_doc[word] = count

In [45]:
occurences_doc["swarovski"]

7

In [46]:
most_common_l["swarovski"]

9

In [47]:
for sent in X_train: #проверяю, что все правильно считается 
    if "swarovski" in mystem_analyzer.lemmatize(sent[0] + " " + sent[1]):
        print(sent)

['светильники потолочный swarovski', 'светильники потолочные swarovski 6 штук , цена за штуку . в эксплуатации 2 года , продаются в связи со сменой интерьера в квартире']
['дубленка женская с шикарным меховым воротом 44р', 'шикарная натуральная дублёнка с меховым воротом и с обалденно красивыми пуговицами . сами пуговицы с кристаллами swarovski , смотрятся нереально красиво 😍, на фото не передалось . в отличном состоянии , почти не носилась .']
['часы женские марки paco rananne оригинал', 'часы женские марки paco rabanne , корпус украшен стразами swarovski . кожаный ремешок , крупные . фирменная коробка , паспорт , индивидуальный номер и чек о покупке']
['купальник для художественной гимнастики', 'купальник для художественной гимнастики . рост 170 - 175 см ./ в хорошем состоянии . украшен только камнями swarovski .']
['клатч " estee lauder " c элементами " swarovski "', 'элегантный клатч известного бренда со стразами swarovski ./ новый ./ синий цвет .']
['daniel wellington 0923dw', '— 


__Задание:__ реализуйте функцию, где тексту в соответствие ставится tf-idf вектор. 

In [48]:
def text_to_tfidf(text: str) -> np.array:
    tf = [text.count(word)/(len(text) + 1e-2) for word in most_common_l.keys()] #тут к длине текста добавяется копеечка, так как 
    #в X_train в строке 332 в title и description стоят по 1. Лемматайзер эти единицы убирает, и длина строки получается 0. 
    #чтобы не вылетала ошибка, была добавлена небольшая копеечка. 
    df = [np.log(len(X_train_conc)/occurences_doc[word]) for word in most_common_l.keys()]
    tf_idf = [t*d for t,d in zip(tf,df)]
    return tf_idf


In [49]:
X_train[332]

['1', '1']

In [50]:
X_train_conc[332]

[]

__Задание:__ а теперь реализуйте функцию, которая преобразует наш датасет и для каждого объекта сопоставляет вектор tf-idf.

In [51]:
def items_to_tfidf(items: np.array) -> np.array:
    """ 
    Для каждого товара возвращает его tfidf вектор
    """
    
    fin = [text_to_tfidf(item) for item in items]
    return fin


In [52]:
X_train_tfidf = items_to_tfidf(X_train_conc)

In [53]:
X_train_tfidf[0]

[0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.4892836209800557,
 0.0,
 0.0,
 0.0,
 0.5781268831760351,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0

In [54]:
X_train_conc[0]

['сапог', 'размер', 'новый', 'сапог', 'размер', 'новый']

In [55]:
X_test_tfidf = items_to_tfidf(X_test_conc)

__Задание:__ обучите логистическую регрессию и SVC, оцените качество (accuracy_score)

In [ ]:
lr_model.fit(X_train_tfidf, y_train)
accuracy_score(lr_model.predict(X_test_tfidf), y_test)

In [ ]:
svc_model.fit(X_train_tfidf, y_train)
accuracy_score(svc_model.predict(X_test_tfidf), y_test)

На этом моменте я решила проверить компилируемость кода, а Юпитер просто вылетел, поэтому результаты не скомпилированы здесь, что безумно обидно :( Я помню, что для СВМ тут получилсь очень хорошие результаты (я об этом пишу еще в последнем пункте), а для регрессии качество было не очень хорошее. Если я правильно помню, для СВМ получилось > 0.8, а регрессия была меньше 0.75 

### Hashing Vectorizer (1 балл)

Попробуйте использовать `sklearn.feature_extraction.text.HashingVectorizer` для векторизации текстов.
Обязательно оцените качество работы алгоритмов классификации с использованием новой векторизации.

In [85]:
from sklearn.feature_extraction.text import HashingVectorizer 

In [34]:
import nltk 
nltk.download("punkt")

[nltk_data] Downloading package punkt to /Users/user/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [111]:
HV = HashingVectorizer(tokenizer = nltk.tokenize.word_tokenize, analyzer = "word")

In [99]:
X_train_hash = [object[0] + " " + object[1] for object in X_train]

In [125]:
X_train_hash = HV.fit_transform(X_train_hash)

In [130]:
X_test_hash = [object[0] + " " + object[1] for object in X_test]

In [131]:
X_test_hash = HV.transform(X_test_hash)

In [132]:
X_test_hash[:5]

<5x1048576 sparse matrix of type '<class 'numpy.float64'>'
	with 204 stored elements in Compressed Sparse Row format>

In [126]:
X_train_hash[:5]

<5x1048576 sparse matrix of type '<class 'numpy.float64'>'
	with 144 stored elements in Compressed Sparse Row format>

In [133]:
lr_model.fit(X_train_hash, y_train)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=100,
                   multi_class='warn', n_jobs=None, penalty='l2',
                   random_state=None, solver='warn', tol=0.0001, verbose=0,
                   warm_start=False)

In [134]:
accuracy_score(lr_model.predict(X_test_hash), y_test) #а качество для регрессии снова падает 

0.6503333333333333

In [135]:
svc_model.fit(X_train_hash, y_train)
accuracy_score(svc_model.predict(X_test_hash), y_test) #самый лучший показатель для свм 

0.8106666666666666

### Word Vectors (3 балла)

Давайте попробуем другой подход -- кажому слову сопоставим какой-то эмбеддинг (вектор).

Вектора будут небольшой размерности. Таким образом мы снизим количество параметров в модели.

Вектора мы возьмём уже готовые (обученные на текстах их интернета), так что наша модель будет знать некоторую дополнительную информацию о внешнем мире.

In [51]:
!wget https://www.dropbox.com/s/0x7oxso6x93efzj/ru.tar.gz

--2020-04-15 15:31:53--  https://www.dropbox.com/s/0x7oxso6x93efzj/ru.tar.gz
Распознаётся www.dropbox.com (www.dropbox.com)… 162.125.70.1
Подключение к www.dropbox.com (www.dropbox.com)|162.125.70.1|:443... соединение установлено.
HTTP-запрос отправлен. Ожидание ответа… 301 Moved Permanently
Адрес: /s/raw/0x7oxso6x93efzj/ru.tar.gz [переход]
--2020-04-15 15:31:54--  https://www.dropbox.com/s/raw/0x7oxso6x93efzj/ru.tar.gz
Повторное использование соединения с www.dropbox.com:443.
HTTP-запрос отправлен. Ожидание ответа… 302 Found
Адрес: https://uc654fc760542e79e40a408488dd.dl.dropboxusercontent.com/cd/0/inline/A14ecAR_USqx1tyj75hVswe6MNx-Z-z1KuiuJWacHUBfwhvQDdhxDEbE7nETgY-ofbOwDOD3jlETGBypjDDcdYd8mq2qksRCIKgpgM2nMDtIGg/file# [переход]
--2020-04-15 15:31:54--  https://uc654fc760542e79e40a408488dd.dl.dropboxusercontent.com/cd/0/inline/A14ecAR_USqx1tyj75hVswe6MNx-Z-z1KuiuJWacHUBfwhvQDdhxDEbE7nETgY-ofbOwDOD3jlETGBypjDDcdYd8mq2qksRCIKgpgM2nMDtIGg/file
Распознаётся uc654fc760542e79e40a408488dd.d

In [56]:
!tar -xzf ru.tar.gz.1

In [59]:
pip install -U gensim

     |████████████████████████████████| 23.7MB 448kB/s eta 0:00:01     |██████████████                  | 10.5MB 2.2MB/s eta 0:00:06     |████████████████████████████▏   | 20.9MB 761kB/s eta 0:00:04     |████████████████████████████▍   | 21.0MB 761kB/s eta 0:00:04
     |████████████████████████████████| 112kB 5.7MB/s eta 0:00:01
     |████████████████████████████████| 133kB 682kB/s eta 0:00:01
     |████████████████████████████████| 6.1MB 5.1MB/s eta 0:00:01
     |████████████████████████████████| 71kB 760kB/s eta 0:00:01
  Created wheel for smart-open: filename=smart_open-1.11.1-cp37-none-any.whl size=95257 sha256=60534d869daec1cd6fabe683b74e11f0baffa3707faed6fce0a4cab5645799d8
  Stored in directory: /Users/user/Library/Caches/pip/wheels/51/88/6c/2bcd305b87c1e62cbcbf419e782ad9fc612cd4bbb71557502d
Successfully built smart-open
Note: you may need to restart the kernel to use updated packages.


In [52]:
import gensim
from gensim.models.wrappers import FastText

model = FastText.load_fasttext_format('ru.bin')

unable to import 'smart_open.gcs', disabling that module


In [53]:
# как мы видим, каждому словву данная модель сопоставляет вектор размерности 300

print(model['привет'].shape)
print(model['привет'])

(300,)
[ 0.02916384  0.02167605  0.05127367 -0.00971958  0.0465235  -0.03945766
  0.02737866  0.00638128 -0.03774629 -0.04257201 -0.00995653  0.02291315
 -0.02301722  0.06697998 -0.03674482 -0.02403202 -0.05404469  0.01372932
  0.00926399 -0.0013149   0.11941359 -0.022448    0.04011497  0.06980549
  0.00407011 -0.09384539  0.03050164 -0.02578281 -0.03525181 -0.06603175
  0.04752798  0.05874675  0.01983666  0.06092105 -0.00957561  0.08307806
 -0.01288903  0.04705157  0.02198839 -0.00649013 -0.0171444   0.03302203
  0.02124882 -0.01902875 -0.05235172  0.03458685 -0.01409259 -0.07477519
  0.01916078  0.02985001  0.0086322   0.03051201  0.02831862  0.04549561
  0.00761138 -0.05459622  0.09056009 -0.08807947 -0.05420396 -0.04793203
 -0.05672329 -0.03025264 -0.03024072 -0.05890108 -0.03137474  0.03292617
  0.05440779 -0.04548327 -0.07266086 -0.09327219  0.07247883  0.0111061
  0.01824225 -0.10570452  0.05110046 -0.04659343 -0.03277056 -0.00803401
 -0.03978698  0.00826598 -0.01074128  0.01843

In [82]:
# Будем рассматривать эмбеддинг предложения, как сумму эмбеддингов токенов

def sentence_embedding(sentence: str) -> np.array:
    """
    Складывает вектора токенов строки sentence
    """
    sentence =  nltk.tokenize.word_tokenize(sentence)
    fin = [0] * 300
    for word in sentence:
        if word in model: 
            fin += model[word]
        else: 
            pass
    return fin

In [84]:
assert np.allclose(sentence_embedding('сдаётся уютный , тёплый гараж для стартапов в ml')[::50],
                   np.array([ 0.08189847,  0.07249198, -0.15601222,  0.03782297,  0.09215296, -0.23092946]))

__Задание:__ сделайте все то же, что в предыдущих пунктах -- реализуйте функцию, которая преобразует данные, а затем обучите логистическую регрессию и SVM, оцените качество.

In [170]:
def title_and_description_vect(items: np.array):
    new = [sentence_embedding(item) for item in items]
    return np.array(new)

In [86]:
X_train_vect = [object[0] + " " + object[1] for object in X_train] #тоже буду работать и с названием, и с описанием
X_test_vect = [object[0] + " " + object[1] for object in X_test]

In [89]:
X_train_vect = title_and_description_vect(X_train_vect)

100%|██████████| 21000/21000 [04:10<00:00, 83.92it/s] 


In [90]:
X_test_vect = title_and_description_vect(X_test_vect)

100%|██████████| 9000/9000 [01:36<00:00, 92.94it/s] 


In [91]:
lr_model.fit(X_train_vect, y_train)
accuracy_score(lr_model.predict(X_test_vect), y_test)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)
/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:929: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


0.5686666666666667

In [96]:
svc_model.fit(X_train_vect, y_train) #точность очень низкая, может с леммами получше будет? 
accuracy_score(svc_model.predict(X_test_vect), y_test)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:929: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


0.5677777777777778

In [164]:
X_train_vect_lemm = [" ".join(X) for X in X_train_conc] #делаю из списков строчки

In [165]:
X_train_vect_lemm[:5]

['сапог размер новый сапог размер новый',
 'светильник потолочный swarovski светильник потолочный swarovski штука цена за штука в эксплуатация год продаваться в связь со смена интерьер в квартира',
 'iphone plus red красный в наличие данный цена только для подписчик instagram iqmac новый красный айфон plus в наличие это элегантный и мощный смартфон который готовый в полный мера раскрывать новый возможность ios аппарат с ядерный процессор и гб озу с легкость решать самый ресурсоемкий задача позволять наслаждаться быстродействие тяжелый приложение и игра на дюймовый дисплей аппарат получать экран как у ipad pro так что картинка теперь соответствовать кинематографический стандарт',
 'пион ирис ромашка рассада пион куст р более шт саженец корень расти у мы более год розовый бордовый и белый на фото цветок п зубчаниновка либо пл революция быть ирис ромашка клубника боярышник и ирга',
 'кофта состояние отличный']

In [174]:
X_test_vect_lemm = [" ".join(X) for X in X_test_conc]

In [171]:
X_train_vect_lemm = title_and_description_vect(X_train_vect_lemm)

In [175]:
X_test_vect_lemm = title_and_description_vect(X_test_vect_lemm)

In [176]:
lr_model.fit(X_train_vect_lemm, y_train) #ну, стало работать чуть получше 
accuracy_score(lr_model.predict(X_test_vect_lemm), y_test)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


0.6138888888888889

In [177]:
svc_model.fit(X_train_vect_lemm, y_train)
accuracy_score(svc_model.predict(X_test_vect_lemm), y_test)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:929: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


0.6158888888888889

### Что дальше? (6 баллов)

Для получения максимальной оценки вам нужно решить любые 2 пункта. Решение каждого пункта даст вам полтора балла:

1. Реализовать N-Gram модели текстовой классификации (__1.5 балла__)

2. Поработать с другими эмбеддингами для слов (например word2vec или GloVe) (__1.5 балла__)

3. Другие способы токенизации (pymorphy2, spaCy) (__1.5 балла__)

4. Добиться качества > 0.765 на тестовых данных (попробуйте другие токенизаторы, предобработку текста, и любые другие идеи, которые вам придут в голову) (__1.5 балла__)

Снабжайте код пояснениями и графиками.
Обязательно необходимо написать вывод по каждому пункту, который вы реализуете.

## 4. 

Качество моделей уже получалось выше 0.765   
Для логистической регресии: 
- при добавления title в  BOW 
- при исползовании Mystem с BOW 

Для СВМ: 
- при нормализации BOW с title и description 
- при использовании Mystem с BOW 
- при использовании TF-IDF для векторизации 
- при использовании HashingVectorizer для векторизации 

## 1.

Я делала это задание до того, как стало известтно, что N-Gramms надо было делать вручную, но так много кода было жалко удалять, поэтому
пусть будет тут :( не обращайте на него внимания 

In [23]:
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer

In [48]:
X_train_grams = [object[0] + " " + object[1] for object in X_train]

In [25]:
from nltk.corpus import stopwords
from string import punctuation
noise = stopwords.words('russian') + list(punctuation)

In [26]:
X_train_grams[:5]

['сапоги 46 размер новые сапоги 46 размер новые',
 'светильники потолочный swarovski светильники потолочные swarovski 6 штук , цена за штуку . в эксплуатации 2 года , продаются в связи со сменой интерьера в квартире',
 'iphone 7 plus 128gb red красный в наличии / / данная цена только для подписчиков instagram : iqmac / / новый красный айфон 7 plus в наличии это элегантный и мощный смартфон , который готов в полной мере раскрыть новые возможности ios 10 . аппарат с 4 - ядерным процессором а10 и 3 гб озу с легкостью решает самые ресурсоемкие задачи , позволяя наслаждаться быстродействием « тяжелых » приложений и игр на 5 , 5 - дюймовом дисплее . аппарат получил экран , как у ipad pro , так что картинка теперь соответствует кинематографическому стандарту .',
 'пион ирис ромашка рассада пион куст 500 р ( более 10 шт )/ саженец / корень 100р / растут у нас более 70 лет / розовые , бордовые и белые / на фото цветы 2018г / п . зубчаниновка / либо пл . революции / есть ирисы , ромашка , клубни

In [27]:
nltk.tokenize.word_tokenize('Но не каждый хочет что-то исправлять:(') #буду использовать этот токенайзер, 
#так как он разделяет знаки пунктуации (как со смайликом) –  легче удалить из даныых, в случае если пунктуация склеена, как .) или )/

['Но', 'не', 'каждый', 'хочет', 'что-то', 'исправлять', ':', '(']

In [29]:
def remove_stopwords(data): #почищу от стоп-слов и пунктуации
    output_array=[] 
    for sentence in data: 
        temp_list=[] 
        for word in nltk.tokenize.word_tokenize(sentence): 
            if word.lower() not in noise:
                temp_list.append(word) 
        output_array.append(' '.join(temp_list)) 
    return output_array

In [49]:
X_train_grams = remove_stopwords(X_train_grams)

In [32]:
X_train_grams[:5]

['сапоги 46 размер новые сапоги 46 размер новые',
 'светильники потолочный swarovski светильники потолочные swarovski 6 штук цена штуку эксплуатации 2 года продаются связи сменой интерьера квартире',
 'iphone 7 plus 128gb red красный наличии данная цена подписчиков instagram iqmac новый красный айфон 7 plus наличии это элегантный мощный смартфон который готов полной мере раскрыть новые возможности ios 10 аппарат 4 ядерным процессором а10 3 гб озу легкостью решает самые ресурсоемкие задачи позволяя наслаждаться быстродействием « тяжелых » приложений игр 5 5 дюймовом дисплее аппарат получил экран ipad pro картинка соответствует кинематографическому стандарту',
 'пион ирис ромашка рассада пион куст 500 р 10 шт саженец корень 100р растут 70 лет розовые бордовые белые фото цветы 2018г п зубчаниновка либо пл революции ирисы ромашка клубника боярышник ирга',
 'кофта состояние отличное']

In [50]:
vectorizer = CountVectorizer(ngram_range=(2,2))

In [51]:
X_train_grams = vectorizer.fit_transform(X_train_grams)

In [37]:
print(X_train_grams.toarray()[:4])

[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]


In [57]:
len(X_train_grams.toarray()[0])

460052

In [52]:
X_test_grams = [object[0] + " " + object[1] for object in X_test]

In [53]:
X_test_grams = remove_stopwords(X_test_grams)

In [54]:
X_test_grams = vectorizer.transform(X_test_grams)

In [55]:
lr_model.fit(X_train_grams, y_train) 
accuracy_score(lr_model.predict(X_test_grams), y_test)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


0.581

In [56]:
svc_model.fit(X_train_grams, y_train) #все довольно плохо. Попробуем еще TF-IDF 
accuracy_score(svc_model.predict(X_test_grams), y_test)

0.6301111111111111

In [58]:
vectorizer_TF = TfidfVectorizer(ngram_range=(2,2))

In [59]:
X_train_grams = [object[0] + " " + object[1] for object in X_train]
X_test_grams = [object[0] + " " + object[1] for object in X_test]

In [60]:
X_train_grams = remove_stopwords(X_train_grams) 
X_test_grams = remove_stopwords(X_test_grams)

In [61]:
X_train_grams = vectorizer_TF.fit_transform(X_train_grams)

In [62]:
X_test_grams = vectorizer_TF.transform(X_test_grams)

In [63]:
lr_model.fit(X_train_grams, y_train) 
accuracy_score(lr_model.predict(X_test_grams), y_test)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


0.5112222222222222

In [64]:
svc_model.fit(X_train_grams, y_train)  #для СВМ стало чуть получше, но не сильно (мы еще раньше убедились, что TF-IDF для СВМ )
#повышает точность)  
accuracy_score(svc_model.predict(X_test_grams), y_test)

0.6844444444444444

Вывод: на этих данных лучше работает токенизация, а не N-граммы 

## 2. 

Я попробую еще word2vec, здесь я тоже буду работать с лемматизированным датасетом. 

In [21]:
from gensim.models import Word2Vec 

unable to import 'smart_open.gcs', disabling that module


In [22]:
import gensim.downloader as api

In [101]:
model = api.load("word2vec-ruscorpora-300")

In [102]:
#чтоб удалить части речи + добавить к ним векторы
new_keys = [k.split("_")[0] for k in list(model.vocab.keys())]
model_new = dict(zip(new_keys, model.vectors))

In [110]:
model_new

{'весь': array([-2.56836211e-04,  1.75269153e-02, -3.54990037e-03, -8.87970068e-03,
        -3.32782306e-02,  1.16420962e-01,  6.11374266e-02, -5.97585291e-02,
        -4.58908416e-02,  7.26233944e-02, -2.99220327e-02,  1.29727647e-01,
        -1.08115815e-01, -1.00786285e-02, -1.79647710e-02,  4.29872982e-02,
         9.22907726e-04, -3.76843400e-02, -6.42695352e-02,  3.14609380e-04,
        -5.39727435e-02, -4.94068637e-02, -1.55055076e-02, -5.18017523e-02,
        -4.85825911e-02, -7.24977031e-02, -7.95320515e-03, -3.40516791e-02,
         5.95795512e-02,  3.82495821e-02,  4.10878323e-02, -1.79348681e-02,
         4.04061191e-02, -7.39418939e-02, -6.18963465e-02,  4.64982959e-03,
        -7.42512420e-02,  4.13340218e-02,  8.39398950e-02,  5.20377122e-02,
         5.09037375e-02,  2.38590706e-02, -7.33022690e-02,  4.56207953e-02,
         7.51752853e-02,  2.53944881e-02, -7.26925163e-03,  4.26316112e-02,
        -2.25173011e-02, -1.29034966e-01, -6.20675609e-02, -4.17450480e-02,
    

In [119]:
def sent_w2v(sentence: str) -> np.array:
    """
    Складывает вектора токенов строки sentence
    """
    sentence =  nltk.tokenize.word_tokenize(sentence)
    fin = [0]*300
    for word in sentence:
        if word in model_new.keys(): 
            fin += model_new[word]
        else: 
            pass
    return fin

In [120]:
def items_w2v(items: np.array):
    new = [sent_w2v(item) for item in items]
    return np.array(new)

In [116]:
X_train_new = [" ".join(X) for X in X_train_conc]

In [122]:
X_train_emb = items_w2v(X_train_new)

In [123]:
X_test_new = [" ".join(X) for X in X_test_conc]

In [125]:
X_test_emb = items_w2v(X_test_new)

In [134]:
lr_model.fit(X_train_emb, y_train) 
accuracy_score(lr_model.predict(X_test_emb), y_test)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


0.76

In [135]:
svc_model.fit(X_train_emb, y_train) #не самый высокий результат, но сильно лучше, чем было в Word Vectors (там результаты были около 0.56)
accuracy_score(svc_model.predict(X_test_emb ), y_test)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:929: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


0.7554444444444445

То есть, модели лучше обучаются на векторах, составленных по данному датасету, а не на готовых эмбеддингах, как word vectorizer или word2vec, – для них результаты были не очень хорошие. 

## 3. 

Я поработаю с pymorphy для лемматизации, посмотрю что изменится

In [35]:
from pymorphy2 import MorphAnalyzer
pymorphy_analyzer = MorphAnalyzer()

In [39]:
text = "шел тридцать третий день карантина...."

In [40]:
text = nltk.word_tokenize(text)

In [41]:
text

['шел', 'тридцать', 'третий', 'день', 'карантина', '...', '.']

In [42]:
text = [pymorphy_analyzer.parse(word)[0].normal_form for word in text]

In [43]:
text #вроде работает! 

['идти', 'тридцать', 'три', 'день', 'карантин', '...', '.']

In [44]:
def preprocess_pm(text: str) -> str:
    text = nltk.word_tokenize(text)
    aux = [pymorphy_analyzer.parse(word)[0].normal_form for word in text]
    return " ".join(aux)

In [45]:
preprocess_pm("сапоги 46 размер новые сапоги 46 размер новые")

'сапог 46 размер новое сапог 46 размер новое'

In [46]:
X_train_pm = [preprocess_pm(x[0]) + " " + preprocess_pm(x[1]) for x in X_train] #сразу склею тайтл и дескрипшн вместе

In [47]:
X_train_pm[:10]

['сапог 46 размер новое сапог 46 размер новое',
 'светильник потолочный swarovski светильник потолочный swarovski 6 штука , цена за штука . в эксплуатация 2 год , продаваться в связь с смена интерьер в квартира',
 'iphone 7 plus 128gb red красный в наличие / / дать цена только для подписчик instagram : iqmac / / новый красный айфон 7 plus в наличие это элегантный и мощный смартфон , который готовый в полный мера раскрыть новое возможность ios 10 . аппарат с 4 - ядерный процессор а10 и 3 гб озу с лёгкость решать самый ресурсоёмкий задача , позволять наслаждаться быстродействие « тяжёлый » приложение и игра на 5 , 5 - дюймовый дисплей . аппарат получить экран , как у ipad pro , так что картинка теперь соответствовать кинематографический стандарт .',
 'пион ирис ромашка рассада пион куст 500 р ( более 10 шт ) / саженец / корень 100р / расти у мы более 70 год / розовый , бордовый и белые / на фото цвета 2018г / плата . зубчаниновка / либо площадь . революция / есть ирис , ромашка , клубник

In [48]:
X_test_pm = [preprocess_pm(x[0]) + " " + preprocess_pm(x[1]) for x in X_test] 

In [49]:
allwords_pm = [tokenizer.tokenize(sent) for sent in X_train_pm]

In [50]:
allwords_pm[:5]

[['сапог', '46', 'размер', 'новое', 'сапог', '46', 'размер', 'новое'],
 ['светильник',
  'потолочный',
  'swarovski',
  'светильник',
  'потолочный',
  'swarovski',
  '6',
  'штука',
  ',',
  'цена',
  'за',
  'штука',
  '.',
  'в',
  'эксплуатация',
  '2',
  'год',
  ',',
  'продаваться',
  'в',
  'связь',
  'с',
  'смена',
  'интерьер',
  'в',
  'квартира'],
 ['iphone',
  '7',
  'plus',
  '128gb',
  'red',
  'красный',
  'в',
  'наличие',
  '/',
  '/',
  'дать',
  'цена',
  'только',
  'для',
  'подписчик',
  'instagram',
  ':',
  'iqmac',
  '/',
  '/',
  'новый',
  'красный',
  'айфон',
  '7',
  'plus',
  'в',
  'наличие',
  'это',
  'элегантный',
  'и',
  'мощный',
  'смартфон',
  ',',
  'который',
  'готовый',
  'в',
  'полный',
  'мера',
  'раскрыть',
  'новое',
  'возможность',
  'ios',
  '10',
  '.',
  'аппарат',
  'с',
  '4',
  '-',
  'ядерный',
  'процессор',
  'а10',
  'и',
  '3',
  'гб',
  'озу',
  'с',
  'лёгкость',
  'решать',
  'самый',
  'ресурсоёмкий',
  'задача',
  ',

In [51]:
allwords_pm = [word for sent in allwords_pm for word in sent]

In [52]:
allwords_pm[:5]

['сапог', '46', 'размер', 'новое', 'сапог']

In [53]:
tokens_pm = {}
for word in allwords_pm: 
    tokens_pm[word] = tokens_pm.get(word, 0) + 1

In [54]:
count_pm = Counter(tokens_pm)
most_common_pm = dict(count_pm.most_common(10000))

In [55]:
def text_to_bow_pm(text: str) -> np.array:
    new = []
    tokens_pm = text.split()
    for i in most_common_pm:
        new.append(tokens_pm.count(i))
    return new

In [56]:
def items_to_bow_pm(items: np.array) -> np.array:
    new = [text_to_bow_pm(item) for item in tqdm(items)]
    return np.array(new)

In [57]:
most_common_pm

{'/': 99549,
 ',': 83061,
 '.': 69273,
 '-': 37370,
 'в': 28853,
 '--': 22517,
 'и': 21714,
 'на': 19465,
 './': 18590,
 ':': 18099,
 '!': 16849,
 ')': 13768,
 'с': 13713,
 '(': 12678,
 'по': 10000,
 'для': 9627,
 'состояние': 6786,
 'не': 6045,
 'весь': 5984,
 '2': 5766,
 '``': 5618,
 '1': 5284,
 'размер': 4543,
 'до': 4541,
 'от': 4483,
 '—': 4463,
 'год': 4440,
 'цена': 4076,
 '3': 4071,
 '5': 4003,
 'у': 3855,
 ';': 3638,
 'новый': 3603,
 'доставка': 3458,
 'за': 3425,
 'без': 3258,
 'наш': 3246,
 'хороший': 3213,
 'вы': 3199,
 'из': 3140,
 'отличный': 3128,
 'рубль': 3124,
 'продать': 2985,
 'запчасть': 2985,
 '*': 2982,
 'наличие': 2967,
 '4': 2939,
 'есть': 2937,
 '00': 2799,
 'сантиметр': 2781,
 'магазин': 2706,
 'к': 2699,
 'мы': 2673,
 'новое': 2642,
 'или': 2631,
 '10': 2452,
 '...': 2427,
 'автомобиль': 2357,
 'б': 2266,
 'метр': 2230,
 '•': 2214,
 'квартира': 2187,
 'звонить': 2159,
 '6': 2126,
 'дом': 2118,
 'при': 2111,
 'комплект': 2083,
 'очень': 2064,
 'компания': 203

In [58]:
text_to_bow_pm("Я устала делать / эту домашку")

[1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,


In [59]:
X_train_bow_pm = items_to_bow_pm(X_train_pm) 
X_test_bow_pm = items_to_bow_pm(X_test_pm)

100%|██████████| 9000/9000 [04:53<00:00, 30.69it/s]


In [60]:
lr_model.fit(X_train_bow_pm, y_train) 
accuracy_score(lr_model.predict(X_test_bow_pm ), y_test)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


0.8046666666666666

In [61]:
svc_model.fit(X_train_bow_pm, y_train) 
accuracy_score(svc_model.predict(X_test_bow_pm ), y_test)

/Users/user/opt/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:929: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


0.7795555555555556

Pymorphy2 дает хорошее качество, причем и для логистической регресии, и для СВМ (несмотря на то, что он анализирует слова отдельно)